In [5]:
import pandas as pd
import numpy as np
import warnings
import os
from pathlib import Path
import matplotlib.pyplot as plt
from statsmodels.tsa.stattools import adfuller, kpss
from statsmodels.graphics.tsaplots import plot_acf, plot_pacf
from statsmodels.stats.diagnostic import acorr_ljungbox
from statsmodels.tsa.seasonal import seasonal_decompose
from scipy.stats import boxcox, normaltest, shapiro
import statsmodels.api as sm
from scipy.signal import find_peaks
from sklearn.linear_model import LinearRegression
from prophet import Prophet
from prophet.diagnostics import cross_validation, performance_metrics
from sklearn.model_selection import ParameterGrid
import statsmodels
import functions_ts
import functions_cancer
import importlib
from datetime import date, time, datetime

importlib.reload(functions_ts)
importlib.reload(functions_cancer)


<module 'functions_cancer' from '/home/jsancheg/git_environment/Europe_Cancer_Incidence/src/data/functions_cancer.py'>

In [6]:
# Obtener el directorio del script

script_dir = Path.cwd()
project_root = script_dir.parent.parent
print(script_dir)

file_path = project_root/ 'data' / 'processed' / 'europe_cancer_cases_long_format.csv'

# 1. Preparación de datos y creación del objecto serie temporal
# ----------------------------------------------------
print('---- Reading the dataset, adding columns day and month to the dataset ----')
df_cancer_incidence = pd.read_csv(file_path)

# Convertir los nombres de columnas a minusculas
df_cancer_incidence.columns = df_cancer_incidence.columns.str.lower()

# Agregar mes y dia al dataset
df_cancer_incidence['month'] = 12
df_cancer_incidence['day'] = 31

# Reordenar columnas
cols = df_cancer_incidence.columns.tolist()
cols.insert(cols.index('year'), cols.pop(cols.index('day')))
cols.insert(cols.index('year'), cols.pop(cols.index('month')))
df_cancer_incidence = df_cancer_incidence[cols]

print ('--- creating column date_reported, and preparing to be used by prophet ---')

# Creer el campo de fecha de reporte y la el campo fecha
df_cancer_incidence['date_reported'] = pd.to_datetime(
    df_cancer_incidence[['year', 'month', 'day']].astype(str).agg('-'.join, axis=1)
)

# La libraria PropPhet require los campos 'ds' y 'y'
df_cancer_incidence['ds'] = df_cancer_incidence['date_reported']
df_cancer_incidence['y'] = df_cancer_incidence['cases_by_age']

cols_date_target = ['date_reported', 'ds', 'y']

cols = df_cancer_incidence.columns.tolist()
for col in reversed(cols_date_target):
    if col in df_cancer_incidence.columns:
        cols.insert(cols.index('age_group') + 1, cols.pop(cols.index(col)))
df_cancer_incidence = df_cancer_incidence[cols]

#print(df_cancer_incidence.columns)
cols_date_target = ['date_reported', 'ds', 'y']

# Reordenar las columnas


for col in reversed(cols_date_target):
    if col in df_cancer_incidence.columns:
        cols.insert(cols.index('age_group') + 1, cols.pop(cols.index(col)))
df_cancer_incidence = df_cancer_incidence[cols]

print(df_cancer_incidence.columns.tolist())



print('--- Printing columns of the dataset and their type ---')
print(df_cancer_incidence.columns)
print(df_cancer_incidence.info()) # Equivalente a str() in R

print('--- Filtering Europe cancer incidences from 2007 - 2017 ---')
df_cancer_incidence_2007_2017 = df_cancer_incidence.query('year >= 2007').copy()
df_cancer_incidence_2000_2010 = df_cancer_incidence.query('year >= 2000').copy()

print(df_cancer_incidence_2007_2017.columns.tolist())
print(df_cancer_incidence_2007_2017[["month","day","year","date_reported","ds"]].head())

print('--- Subseting the series to be forecasted by cancer type, sex, and age group ---')

item_id = df_cancer_incidence_2007_2017[
    ["cancer_classification", "sex_character","age_group"]
].drop_duplicates().reset_index(drop=True)


/home/jsancheg/git_environment/Europe_Cancer_Incidence/src/data
---- Reading the dataset, adding columns day and month to the dataset ----
--- creating column date_reported, and preparing to be used by prophet ---
['cancer_classification', 'sex_character', 'day', 'month', 'year', 'age_group', 'date_reported', 'ds', 'y', 'cases_by_age', 'total']
--- Printing columns of the dataset and their type ---
Index(['cancer_classification', 'sex_character', 'day', 'month', 'year',
       'age_group', 'date_reported', 'ds', 'y', 'cases_by_age', 'total'],
      dtype='object')
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 71630 entries, 0 to 71629
Data columns (total 11 columns):
 #   Column                 Non-Null Count  Dtype         
---  ------                 --------------  -----         
 0   cancer_classification  71630 non-null  object        
 1   sex_character          71630 non-null  object        
 2   day                    71630 non-null  int64         
 3   month               

In [7]:
print(type(item_id))
print(item_id.iloc[0])

<class 'pandas.core.frame.DataFrame'>
cancer_classification    All cancers but non-melanoma skin (C00-96, but...
sex_character                                                            M
age_group                                                             N0_4
Name: 0, dtype: object


In [16]:
aux_serie = functions_cancer.filtering_item(df_cancer_incidence_2007_2017, item_id.iloc[[0]])

n_point_scale = 0.05
n_seasonality_scale = 10.0
n_ci = 0.95
n_samples = 1000
n_periods = 30
n_freq = 'D'


for index, row in item_id.iterrows():
    aux_serie = functions_cancer.filtering_item(df_cancer_incidence_2007_2017, item_id.iloc[[index]])
    print(aux_serie)
    serie = aux_serie[['ds','y']]
    print(f"serie {index + 1} - {row}")
    modelo = Prophet(
        growth = 'linear',
        yearly_seasonality = True,
        weekly_seasonality = True,
        daily_seasonality = True,
        seasonality_mode = 'additive',
        changepoint_prior_scale = n_point_scale,
        seasonality_prior_scale = n_seasonality_scale,
        interval_width = n_ci,
        uncertainty_samples = n_samples
    )

    modelo.fit(serie)
    future = modelo.make_future_dataframe(
        periods = n_periods,
        freq = n_freq
    )

    print("\nGenerating predictions ...")
    forecast = modelo.predict(future)
    future_forecast = forecast[['ds', 'yhat', 'yhat_lower', 'yhat_upper']].tail(30).copy()
    print("\n30 dias forecast")
    print(future_forecast)
    
    
    
    

17:54:45 - cmdstanpy - INFO - Chain [1] start processing


                                cancer_classification sex_character  day  \
54  All cancers but non-melanoma skin (C00-96, but...             M   31   
55  All cancers but non-melanoma skin (C00-96, but...             M   31   
56  All cancers but non-melanoma skin (C00-96, but...             M   31   
57  All cancers but non-melanoma skin (C00-96, but...             M   31   
58  All cancers but non-melanoma skin (C00-96, but...             M   31   
59  All cancers but non-melanoma skin (C00-96, but...             M   31   
60  All cancers but non-melanoma skin (C00-96, but...             M   31   
61  All cancers but non-melanoma skin (C00-96, but...             M   31   
62  All cancers but non-melanoma skin (C00-96, but...             M   31   
63  All cancers but non-melanoma skin (C00-96, but...             M   31   
64  All cancers but non-melanoma skin (C00-96, but...             M   31   

    month  year age_group date_reported         ds     y  cases_by_age   total  
54    

17:54:45 - cmdstanpy - INFO - Chain [1] done processing
17:54:45 - cmdstanpy - INFO - Chain [1] start processing



Generating predictions ...

30 dias forecast
           ds          yhat    yhat_lower    yhat_upper
11 2018-01-01   1014.334274   1014.334273   1014.334275
12 2018-01-02   1244.943050   1244.943049   1244.943051
13 2018-01-03   1503.149639   1503.149638   1503.149640
14 2018-01-04   1957.532461   1957.532460   1957.532462
15 2018-01-05   2540.550669   2540.550669   2540.550670
16 2018-01-06   3235.971884   3235.971883   3235.971885
17 2018-01-07   4171.372169   4171.372168   4171.372169
18 2018-01-08   5122.110443   5122.110442   5122.110444
19 2018-01-09   6347.844421   6347.844420   6347.844422
20 2018-01-10   7576.100701   7576.100700   7576.100702
21 2018-01-11   8946.505414   8946.505413   8946.505415
22 2018-01-12  10363.143803  10363.143802  10363.143804
23 2018-01-13  11782.717484  11782.717483  11782.717485
24 2018-01-14  13307.744409  13307.744408  13307.744409
25 2018-01-15  14691.185846  14691.185845  14691.185847
26 2018-01-16  16173.550879  16173.550878  16173.550879
27

17:54:46 - cmdstanpy - INFO - Chain [1] done processing
17:54:46 - cmdstanpy - INFO - Chain [1] start processing
17:54:46 - cmdstanpy - INFO - Chain [1] done processing


...


Generating predictions ...

30 dias forecast
           ds       yhat  yhat_lower  yhat_upper
11 2018-01-01   0.205849   -0.362099    0.813151
12 2018-01-02   1.817020    1.260676    2.409643
13 2018-01-03   2.239029    1.665423    2.823080
14 2018-01-04   3.493209    2.930822    4.127247
15 2018-01-05   6.547483    5.940308    7.112857
16 2018-01-06   6.316760    5.737822    6.884934
17 2018-01-07   9.334775    8.743906    9.938777
18 2018-01-08  10.459621    9.882214   11.029372
19 2018-01-09  13.727007   13.126643   14.274664
20 2018-01-10  15.500295   14.885588   16.075496
21 2018-01-11  17.766522   17.204470   18.365333
22 2018-01-12  21.468107   20.894079   22.033049
23 2018-01-13  21.503886   20.902573   22.071200
24 2018-01-14  24.401339   23.807068   24.956658
25 2018-01-15  25.022257   24.442027   25.603850
26 2018-01-16  27.415857   26.841672   28.023010
27 2018-01-17  27.968431   27.406840   28.525529
28 2018-01-18  28.698720   28.185061   29.255627
29 2018-01-19  30.58875

18:06:14 - cmdstanpy - INFO - Chain [1] done processing
18:06:14 - cmdstanpy - INFO - Chain [1] start processing
18:06:14 - cmdstanpy - INFO - Chain [1] done processing



Generating predictions ...

30 dias forecast
           ds      yhat  yhat_lower  yhat_upper
11 2018-01-01  0.005232    0.005232    0.005232
12 2018-01-02  1.022694    1.022694    1.022694
13 2018-01-03  0.058119    0.058119    0.058119
14 2018-01-04  0.116780    0.116780    0.116780
15 2018-01-05  0.204334    0.204334    0.204334
16 2018-01-06  0.323292    0.323292    0.323292
17 2018-01-07  0.477053    0.477053    0.477053
18 2018-01-08  0.667853    0.667853    0.667853
19 2018-01-09  1.895564    1.895564    1.895564
20 2018-01-10  1.160165    1.160165    1.160165
21 2018-01-11  1.460575    1.460575    1.460575
22 2018-01-12  1.795633    1.795633    1.795633
23 2018-01-13  2.160691    2.160691    2.160691
24 2018-01-14  2.551786    2.551786    2.551786
25 2018-01-15  2.963714    2.963714    2.963714
26 2018-01-16  4.388965    4.388965    4.388965
27 2018-01-17  3.820315    3.820315    3.820315
28 2018-01-18  4.249791    4.249791    4.249791
29 2018-01-19  4.669760    4.669760    4.6

18:06:14 - cmdstanpy - INFO - Chain [1] start processing
18:06:14 - cmdstanpy - INFO - Chain [1] done processing
18:06:14 - cmdstanpy - INFO - Chain [1] start processing
18:06:14 - cmdstanpy - INFO - Chain [1] done processing



Generating predictions ...

30 dias forecast
           ds       yhat  yhat_lower  yhat_upper
11 2018-01-01  -0.296496   -0.742917    0.120199
12 2018-01-02  -1.679832   -2.099915   -1.258965
13 2018-01-03  -2.111691   -2.512258   -1.698566
14 2018-01-04  -2.832042   -3.251126   -2.429946
15 2018-01-05  -4.822346   -5.247281   -4.386373
16 2018-01-06  -5.797725   -6.190456   -5.390175
17 2018-01-07  -5.757235   -6.143871   -5.356147
18 2018-01-08  -7.156568   -7.551237   -6.747246
19 2018-01-09  -8.498290   -8.910884   -8.081308
20 2018-01-10  -8.743980   -9.154100   -8.343856
21 2018-01-11  -9.137016   -9.545352   -8.717879
22 2018-01-12 -10.665667  -11.061770  -10.248905
23 2018-01-13 -11.055092  -11.441456  -10.632849
24 2018-01-14 -10.317369  -10.732829   -9.912632
25 2018-01-15 -10.923868  -11.326488  -10.511261
26 2018-01-16 -11.395096  -11.796335  -10.989834
27 2018-01-17 -10.712391  -11.130894  -10.312201
28 2018-01-18 -10.140203  -10.527075   -9.715359
29 2018-01-19 -10.68866

                                cancer_classification sex_character  day  \
54  All cancers but non-melanoma skin (C00-96, but...             M   31   
55  All cancers but non-melanoma skin (C00-96, but...             M   31   
56  All cancers but non-melanoma skin (C00-96, but...             M   31   
57  All cancers but non-melanoma skin (C00-96, but...             M   31   
58  All cancers but non-melanoma skin (C00-96, but...             M   31   
59  All cancers but non-melanoma skin (C00-96, but...             M   31   
60  All cancers but non-melanoma skin (C00-96, but...             M   31   
61  All cancers but non-melanoma skin (C00-96, but...             M   31   
62  All cancers but non-melanoma skin (C00-96, but...             M   31   
63  All cancers but non-melanoma skin (C00-96, but...             M   31   
64  All cancers but non-melanoma skin (C00-96, but...             M   31   

    month  year age_group date_reported         ds     y  cases_by_age   total  
54    